In [1]:
# La clase `Model` se hace cargo de los atributos a nivel del modelo, maneja los agentes. 
# Cada modelo puede contener múltiples agentes y todos ellos son instancias de la clase `Agent`.
from mesa import Agent, Model 

# Debido a que necesitamos un solo agente por celda elegimos `SingleGrid` que fuerza un solo objeto por celda.
from mesa.space import MultiGrid

# Con `SimultaneousActivation` hacemos que todos los agentes se activen de manera simultanea.
from mesa.time import SimultaneousActivation

# Vamos a hacer uso de `DataCollector` para obtener el grid completo cada paso (o generación) y lo usaremos para graficarlo.
from mesa.datacollection import DataCollector

# mathplotlib lo usamos para graficar/visualizar como evoluciona el autómata celular.
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as animation
plt.rcParams["animation.html"] = "jshtml"
matplotlib.rcParams['animation.embed_limit'] = 2**128

# Definimos los siguientes paquetes para manejar valores númericos.
import numpy as np
import pandas as pd

import itertools

# Definimos otros paquetes que vamos a usar para medir el tiempo de ejecución de nuestro algoritmo.
import time
import datetime

In [59]:
def get_grid(model):
    dimensions = model.grid.width, model.grid.height
    grid = np.zeros(dimensions)
    for x, line in enumerate(grid):
        for y, _ in enumerate(line):
            # amount of dirt agents in cell
            dirt = len(list(filter(lambda agent: isinstance(agent,DirtAgent) and not agent.is_clean, model.grid.iter_neighbors((x,y), False, True, 0))))
            #print(f'{x=} {y=} {dirt=}')
            # len of dirt agents in cell
            vacuums = len(list(filter(lambda agent: isinstance(agent,VacuumAgent), model.grid.iter_neighbors((x,y), False, True, 0))))
            #print(f'{vacuums=}')
            if dirt != 0 and vacuums == 0:
                grid[x][y] = -10
            elif dirt == 0 and vacuums != 0:
                grid[x][y] = 10
            elif dirt != 0 and vacuums != 0:
                grid[x][y] = 5
            elif dirt == 0 and vacuums == 0:
                grid[x][y] = 0
        
    return grid

def get_dirt_amount(model):
    return model.dirt_amount

class VacuumAgent(Agent):
    def __init__(self,id, x, y, model):
        super().__init__(id,model)
        self.id = id
        self.coords = x,y
        self.model = model
        self.next_pos = None
        self.total_steps = 0
    
    def step(self):
        need_to_clean = any([isinstance(agent,DirtAgent) and not agent.is_clean for agent in self.model.grid.iter_neighbors(self.coords, False, True, 0)])
        if not need_to_clean:
            valid_neighborhood = [cell for cell in self.model.grid.iter_neighborhood(self.coords,True,False,1)]
            # insert current coords to replace unreachable space
            valid_neighborhood.extend([self.coords for _ in range(8-len(valid_neighborhood))])
            
            choices = valid_neighborhood
            # choose next position
            self.next_pos =choices[np.random.choice(len(choices))]
        else:
            self.next_pos = self.coords
    def advance(self):
        if self.next_pos != self.coords:
            self.total_steps = self.total_steps + 1
        self.coords = self.next_pos
        self.model.grid.move_agent(self,self.coords)

class DirtAgent(Agent):
    def __init__(self,id, x, y, model):
        super().__init__(id, model)
        self.id = id
        self.coords = x, y
        self.model = model
        self.next_state = None
        self.is_clean = False
        
    def step(self):
        # if there are any vacuum agents in the same cell next state is clean
        if not self.is_clean:
            self.next_state = any([isinstance(agent,VacuumAgent) for agent in self.model.grid.iter_neighbors(self.coords, False, True, 0)])
            if self.next_state == True:
                self.model.dirt_amount = self.model.dirt_amount-1
        
    def advance(self):
        self.is_clean = self.is_clean or self.next_state
        
class CleaningModel(Model):
    def __init__(self,M,N,vacuums,dirty_percentage):
        self.grid = MultiGrid(M,N,False)
        self.schedule = SimultaneousActivation(self)
        self.dirt_amount = int(M*N*(dirty_percentage*100))//100
        print(f'{self.dirt_amount=}')
        id = 0
        shuffled_dirt_coords = list(self.grid.coord_iter())
        np.random.shuffle(shuffled_dirt_coords)
        for (content, x, y) in shuffled_dirt_coords[:self.dirt_amount]:
            a = DirtAgent(id, x, y, self)
            self.grid.place_agent(a, (x, y))
            self.schedule.add(a)
            id = id + 1
        
        for _ in itertools.repeat(None,vacuums):
            a = VacuumAgent(id, 1, 1, self)
            self.grid.place_agent(a, (1, 1))
            self.schedule.add(a)
            id = id + 1
    
                
        self.datacollector = DataCollector(
            model_reporters={"Grid": get_grid,})
    def step(self):
        self.datacollector.collect(self)
        self.schedule.step()

In [60]:
M = 20
N = 20
num_aspiradoras = 5
porc_celdas_sucias = 0.6

tiempo_ejecucion = 1

gens = 0
start_time = time.time()
model = CleaningModel(M,N,num_aspiradoras,porc_celdas_sucias)
while (time.time() - start_time < tiempo_ejecucion):
    gens = gens + 1
    model.step()
print(f'{model.dirt_amount=}')
for idx, agent in enumerate(model.schedule.agent_buffer()):
    if isinstance(agent,VacuumAgent):
        print(f'El agente {idx} se movio {agent.total_steps} pasos')
    # Imprimimos el tiempo que le tomó correr al modelo.
print('Tiempo de ejecución:', str(datetime.timedelta(seconds=(time.time() - start_time))))

self.dirt_amount=240
model.dirt_amount=69
El agente 240 se movio 234 pasos
El agente 241 se movio 267 pasos
El agente 242 se movio 220 pasos
El agente 243 se movio 260 pasos
El agente 244 se movio 244 pasos
Tiempo de ejecución: 0:00:01.003909


In [56]:
all_grid = model.datacollector.get_model_vars_dataframe()
all_grid

Grid
0    [[-10.0, 0.0, -10.0, 0.0, 0.0, 0.0, -10.0, 0.0...
1    [[-10.0, 0.0, -10.0, 0.0, 0.0, 0.0, -10.0, 0.0...
2    [[5.0, 0.0, -10.0, 0.0, 0.0, 0.0, -10.0, 0.0, ...
3    [[10.0, 0.0, -10.0, 0.0, 0.0, 0.0, -10.0, 0.0,...
4    [[10.0, 0.0, -10.0, 0.0, 0.0, 0.0, -10.0, 0.0,...
..                                                 ...
343  [[0.0, 0.0, 0.0, 10.0, 0.0, 0.0, 0.0, 0.0, 0.0...
344  [[0.0, 0.0, 0.0, 0.0, 10.0, 0.0, 0.0, 0.0, 0.0...
345  [[0.0, 0.0, 0.0, 0.0, 10.0, 0.0, 0.0, 0.0, 0.0...
346  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...
347  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...

[348 rows x 1 columns]

In [53]:
%%capture

fig, axs = plt.subplots(figsize=(M,N))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap=plt.cm.coolwarm)

def animate(i):
    patch.set_data(all_grid.iloc[i][0])
    
anim = animation.FuncAnimation(fig, animate, frames=gens)

In [54]:
anim